# Installation

In [ ]:
import numpy as np
import pandas as pd
import re
import gdown

In [ ]:
!mkdir -p data

In [ ]:
file_id = '1iFU-jK5zROLR1xnb3WnT0u0qjZeq58Z7'
url = f'https://drive.google.com/uc?id={file_id}'
output = 'data/general_info_v3.csv'
gdown.download(url, output, quiet=False )

Downloading...
From: https://drive.google.com/uc?id=1iFU-jK5zROLR1xnb3WnT0u0qjZeq58Z7
To: /content/data/general_info_v3.csv
100%|██████████| 1.52M/1.52M [00:00<00:00, 43.1MB/s]


'data/general_info_v3.csv'

In [ ]:
df_general_v2 = pd.read_csv('data/general_info_v3.csv')


In [ ]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.max_colwidth', None)

# Check laptop_variant

In [ ]:
file_id = "1CIbqME8HqdJ_QY9mMtnsiWmKFU_3tWJx"
url = f"https://drive.google.com/uc?id={file_id}"
output = "data/laptop_price_color.csv"
gdown.download(url, output, quiet=False)

Downloading...
From: https://drive.google.com/uc?id=1CIbqME8HqdJ_QY9mMtnsiWmKFU_3tWJx
To: /content/data/laptop_price_color.csv
100%|██████████| 697k/697k [00:00<00:00, 85.6MB/s]


'data/laptop_price_color.csv'

In [ ]:
df_variant = pd.read_csv("data/laptop_price_color.csv")

# Merge laptop & variants

In [ ]:
file_id = "12l9A9o69S71RCvT2sCGPLUUF1ux3FPje"
url = f"https://drive.google.com/uc?id={file_id}"
output = "data/general_info_v3.csv"
gdown.download(url, output, quiet=False)


Downloading...
From: https://drive.google.com/uc?id=12l9A9o69S71RCvT2sCGPLUUF1ux3FPje
To: /content/data/general_info_v3.csv
100%|██████████| 1.53M/1.53M [00:00<00:00, 126MB/s]


'data/general_info_v3.csv'

In [ ]:
df_general_v3 = pd.read_csv('data/general_info_v3.csv')

In [ ]:
df_general_v3.columns

Index(['product_id', 'name', 'image', 'display_size', 'storage_gb',
       'key_selling_points', 'cam_ung', 'material', 'laptop_special_feature',
       'laptop_nganh_hoc', 'ram_storage', 'ram_max_support', 'product_state',
       'storage_max_support', 'nhu_cau_su_dung', 'manufacturer',
       'filter_label', 'cpu_brand', 'is_installment', 'filter_id',
       'warranty_info', 'product_weight', 'url_path', 'url_key', 'os_version',
       'display_width', 'vga_brand', 'bluetooth_version', 'has_bluetooth',
       'display_height', 'ram_type', 'cpu_series', 'o_cung_laptop', 'vga_type',
       'ports_slots', 'width_mm', 'height_mm', 'depth_mm', 'display_type',
       'battery_capacity', 'laptop_camera', 'laptop_cong_nghe_am_thanh',
       'ram_slots', 'cpu_model', 'ram_speed', 'cpu_cores',
       'laptop_tam_nen_man_hinh', 'root_price', 'discounted_price',
       'cpu_max_speed', 'refresh_rate', 'cpu_threads', 'cpu_speed',
       'vga_vram'],
      dtype='object')

In [ ]:
if df_general_v3['product_id'].dtypes != df_variant['root-laptop_id'].dtypes:
  print("Error: Data types do not match")
  df_general_v3['product_id'] = df_general_v3['product_id'].astype(int)
  df_variant['root-laptop_id'] = df_variant['root-laptop_id'].astype(int)

# LEFT JOIN with left side is df_general_v3 --> keep all
merged_df = pd.merge(df_general_v3, df_variant,
                     how = 'left',
                     left_on = 'product_id',
                     right_on = 'root-laptop_id',
                     suffixes = ('_general', '_variant') # add suffix for same-name columns
                     )

In [ ]:
print(f"Số dòng trong DataFrame đã merge: {len(merged_df)}")

Số dòng trong DataFrame đã merge: 903


# Fixing (1) + (2)

In [ ]:
merged_df.columns

Index(['product_id', 'name', 'display_size', 'storage_gb', 'cam_ung',
       'key_selling_points', 'material', 'laptop_nganh_hoc', 'refresh_rate',
       'ram_storage', 'laptop_tam_nen_man_hinh', 'ram_max_support',
       'product_state', 'storage_max_support', 'nhu_cau_su_dung',
       'manufacturer', 'filter_label', 'cpu_brand', 'is_installment',
       'filter_id', 'warranty_information', 'product_weight', 'url_path',
       'vga_vram', 'vga_brand', 'ram_speed', 'ram_slots', 'ram_type',
       'cpu_cores', 'cpu_model', 'cpu_series', 'display_width', 'os_version',
       'display_height', 'bluetooth_version', 'width_mm', 'battery_capacity',
       'height_mm', 'depth_mm', 'laptop_camera', 'vga_type', 'has_bluetooth',
       'o_cung_laptop', 'ports_slots', 'laptop_screen_size_filter',
       'display_type', 'laptop_cong_nghe_am_thanh', 'laptop_special_feature',
       'root_price', 'discounted_price', 'cpu_threads', 'child_laptop_image',
       'child_laptop_link', 'laptop_color'],
  

## product_id
* if (root-laptop_id): product_id = child-laptop_id
* else: product_id = product-id
* delete root-laptop_id and child-laptoop_id

In [ ]:
merged_df['product_id'] = merged_df.apply(
    lambda row: row['child-laptop_id'] if pd.notna(row['root-laptop_id']) else row['product_id'],
    axis=1
)


In [ ]:
merged_df[['product_id','root-laptop_id','child-laptop_id']]

product_id  root-laptop_id  child-laptop_id
0       75444.0         75443.0          75444.0
1       86461.0         49568.0          86461.0
2       86460.0         49568.0          86460.0
3       86462.0         49568.0          86462.0
4       86459.0         49568.0          86459.0
5      101837.0        101832.0         101837.0
6      101838.0        101832.0         101838.0
7      101835.0        101832.0         101835.0
8      101836.0        101832.0         101836.0
9       91455.0         91451.0          91455.0
10     100666.0        100664.0         100666.0
11      94501.0         78296.0          94501.0
12      94504.0         78296.0          94504.0
13      94503.0         78296.0          94503.0
14      94502.0         78296.0          94502.0
15      87099.0         87098.0          87099.0
16      79552.0         79551.0          79552.0
17     101843.0        101839.0         101843.0
18     101842.0        101839.0         101842.0
19     101841.0        101839.0         101841.0
20     101840.0        101839.0         101840.0
21      94086.0         94083.0          94086.0
22      94085.0         94083.0          94085.0
23      99129.0         99127.0          99129.0
24      93963.0         93958.0          93963.0
25      82906.0         82905.0          82906.0
26      76752.0         76751.0          76752.0
27      79241.0         79238.0          79241.0
28      95113.0         95111.0          95113.0
29      95114.0         95111.0          95114.0
30      95115.0         95111.0          95115.0
31      95112.0         95111.0          95112.0
32      42450.0         42449.0          42450.0
33      71866.0         71865.0          71866.0
34      86211.0         86208.0          86211.0
35      73001.0         73000.0          73001.0
36      73002.0         73000.0          73002.0
37      75068.0         75064.0          75068.0
38      87617.0         86451.0          87617.0
39      87618.0         86451.0          87618.0
40      87616.0         86451.0          87616.0
41      86452.0         86451.0          86452.0
42      88378.0         88377.0          88378.0
43      94105.0         94091.0          94105.0
44      94104.0         94091.0          94104.0
45      65169.0         65165.0          65169.0
46      62666.0         62665.0          62666.0
47      61494.0         61491.0          61494.0
48      97893.0         97885.0          97893.0
49      86710.0         86709.0          86710.0
50      49569.0         86458.0          49569.0
51      49572.0         86458.0          49572.0
52      49570.0         86458.0          49570.0
53      49571.0         86458.0          49571.0
54      87096.0         87095.0          87096.0
55      83572.0         83458.0          83572.0
56      94522.0         94521.0          94522.0
57      87572.0         87571.0          87572.0
58      69472.0         69467.0          69472.0
59      86031.0         86030.0          86031.0
60      86132.0         86131.0          86132.0
61      75606.0         75605.0          75606.0
62      88414.0         88413.0          88414.0
63      83797.0         83796.0          83797.0
64      92247.0         92246.0          92247.0
65      62448.0             NaN              NaN
66      63053.0         63052.0          63053.0
67      49575.0         49574.0          49575.0
68      49577.0         49574.0          49577.0
69      49578.0         49574.0          49578.0
70      49576.0         49574.0          49576.0
71      83795.0         83731.0          83795.0
72      94461.0         94459.0          94461.0
73     101868.0        101867.0         101868.0
74      62671.0         62669.0          62671.0
75      78302.0         94500.0          78302.0
76      78301.0         94500.0          78301.0
77      82086.0         94500.0          82086.0
78      78300.0         94500.0          78300.0
79      70433.0         70430.0          70433.0
80     101848.0        101844.0     

In [ ]:
# check if there is any duplicate in 'product_id' column

if merged_df['product_id'].duplicated().any():
  print("There are duplicate product_id values.")
else:
  print("There are no duplicate product_id values.")

There are no duplicate product_id values.


In [ ]:
merged_df.drop(columns=['root-laptop_id', 'child-laptop_id'], inplace=True)

In [ ]:
print(f'Null: {merged_df["product_id"].isna().sum()}')

Null: 0


## name & child-laptop_name

In [ ]:
merged_df[['name', 'child_laptop_name']]

name  \
0                                           Laptop Gaming Acer Nitro V ANV15-51-58AN   
1            Apple MacBook Air M2 2024 8CPU 8GPU 16GB 256GB I Chnh hng Apple Vit Nam   
2            Apple MacBook Air M2 2024 8CPU 8GPU 16GB 256GB I Chnh hng Apple Vit Nam   
3            Apple MacBook Air M2 2024 8CPU 8GPU 16GB 256GB I Chnh hng Apple Vit Nam   
4            Apple MacBook Air M2 2024 8CPU 8GPU 16GB 256GB I Chnh hng Apple Vit Nam   
5                                  MacBook Air M4 13 inch 2025 10CPU 8GPU 16GB 256GB   
6                                  MacBook Air M4 13 inch 2025 10CPU 8GPU 16GB 256GB   
7                                  MacBook Air M4 13 inch 2025 10CPU 8GPU 16GB 256GB   
8                                  MacBook Air M4 13 inch 2025 10CPU 8GPU 16GB 256GB   
9                                         Laptop ASUS TUF Gaming A15 FA506NCR-HN047W   
10                                                          Laptop HP 250 G9 AG2K7AT   
11                         MacBook Air M3 13 inch 2024 8CPU 8GPU 16GB - 256GB sc 30W   
12                         MacBook Air M3 13 inch 2024 8CPU 8GPU 16GB - 256GB sc 30W   
13                         MacBook Air M3 13 inch 2024 8CPU 8GPU 16GB - 256GB sc 30W   
14                         MacBook Air M3 13 inch 2024 8CPU 8GPU 16GB - 256GB sc 30W   
15                                Laptop Acer Aspire Lite AL16-51P-55N7 NX.KX0SV.001   
16                                      Laptop ASUS  Vivobook 14 OLED A1405VA-KM257W   
17                                MacBook Air M4 13 inch 2025 10CPU 10GPU 16GB 512GB   
18                                MacBook Air M4 13 inch 2025 10CPU 10GPU 16GB 512GB   
19                                MacBook Air M4 13 inch 2025 10CPU 10GPU 16GB 512GB   
20                                MacBook Air M4 13 inch 2025 10CPU 10GPU 16GB 512GB   
21                                          MacBook Pro 14 M4 10CPU 10GPU 16GB 512GB   
22                                          MacBook Pro 14 M4 10CPU 10GPU 16GB 512GB   
23                                       Laptop HP Gaming Victus 15-FA1139TX 8Y6W3PA   
24                                           Mac mini M4 2024 10CPU 10GPU 16GB 256GB   
25                                        Laptop ASUS TUF Gaming F15 FX507ZC4-HN095W   
26                                               Laptop Lenovo LOQ 15IAX9 83GS000RVN   
27                                            Laptop ASUS Vivobook 15 X1504ZA-NJ517W   
28                          MacBook Air M3 15 inch 2024 8CPU 10GPU 24GB 512GB Sc 35W   
29                          MacBook Air M3 15 inch 2024 8CPU 10GPU 24GB 512GB Sc 35W   
30                          MacBook Air M3 15 inch 2024 8CPU 10GPU 24GB 512GB Sc 35W   
31                          MacBook Air M3 15 inch 2024 8CPU 10GPU 24GB 512GB Sc 35W   
32                                    Laptop Gaming Acer Nitro 5 Tiger AN515 58 52SP   
33                                          Laptop Acer Gaming Aspire 7 A715-76-53PJ   
34                                        Laptop ASUS Gaming VivoBook K3605ZC-RP564W   
35                                                  MacBook Pro 16 M3 Max 48GB - 1TB   
36                                                  MacBook Pro 16 M3 Max 48GB - 1TB   
37                                        Laptop Dell Inspiron 15 3520-5810BLK 102F0   
38   Apple MacBook Air M2 2024 8CPU 10GPU 16GB 512GB Sc 70W I Chnh hng Apple Vit Nam   
39   Apple MacBook Air M2 2024 8CPU 10GPU 16GB 512GB Sc 70W I Chnh hng Apple Vit Nam   
40   Apple MacBook Air M2 2024 8CPU 10GPU 16GB 512GB Sc 70W I Chnh hng Apple Vit Nam   
41   Apple MacBook Air M2 2024 8CPU 10GPU 16GB 512GB Sc 70W I Chnh hng Apple Vit Nam   
42                                                Laptop Dell Inspiron 15 3520 6HD73   
43                                      MacBook Pro 14 M4 Pro 12CPU 16GPU 24GB 512GB   
44                                      MacBook Pro 14 M4 Pro 12CPU 16GPU 24GB 512GB   
45                              

In [ ]:
merged_df['name'] = merged_df.apply(
    lambda row: row['child_laptop_name'] if pd.notna(row['child_laptop_name']) else row['name'],
    axis=1
)

In [ ]:
print(f'Null: {merged_df["name"].isna().sum()}')

Null: 0


In [ ]:
merged_df.drop(columns = ['child_laptop_name'], inplace=True)

## url_key, url_path, child_laptop_link

In [ ]:
merged_df['child_laptop_link']

0                                  /laptop-gaming-acer-nitro-v-anv15-51-58an.html?product_id=75444
1                                                  /macbook-air-m2-2022-16gb.html?product_id=86461
2                                                  /macbook-air-m2-2022-16gb.html?product_id=86460
3                                                  /macbook-air-m2-2022-16gb.html?product_id=86462
4                                                  /macbook-air-m2-2022-16gb.html?product_id=86459
5                       /apple-macbook-air-13-m4-10cpu-8gpu-16gb-256gb-2025.html?product_id=101837
6                       /apple-macbook-air-13-m4-10cpu-8gpu-16gb-256gb-2025.html?product_id=101838
7                       /apple-macbook-air-13-m4-10cpu-8gpu-16gb-256gb-2025.html?product_id=101835
8                       /apple-macbook-air-13-m4-10cpu-8gpu-16gb-256gb-2025.html?product_id=101836
9                                /laptop-asus-tuf-gaming-a15-fa506ncr-hn047w.html?product_id=91455
10                                                /laptop-hp-250-g9-ag2k7at.html?product_id=100666
11                                   /macbook-air-m3-13-inch-2024-16gb-256gb.html?product_id=94501
12                                   /macbook-air-m3-13-inch-2024-16gb-256gb.html?product_id=94504
13                                   /macbook-air-m3-13-inch-2024-16gb-256gb.html?product_id=94503
14                                   /macbook-air-m3-13-inch-2024-16gb-256gb.html?product_id=94502
15                                    /laptop-acer-aspire-lite-al16-51p-55n7.html?product_id=87099
16                              /laptop-asus-vivobook-14-oled-a1405va-km257w.html?product_id=79552
17                     /apple-macbook-air-13-m4-10cpu-10gpu-16gb-512gb-2025.html?product_id=101843
18                     /apple-macbook-air-13-m4-10cpu-10gpu-16gb-512gb-2025.html?product_id=101842
19                     /apple-macbook-air-13-m4-10cpu-10gpu-16gb-512gb-2025.html?product_id=101841
20                     /apple-macbook-air-13-m4-10cpu-10gpu-16gb-512gb-2025.html?product_id=101840
21                                        /macbook-pro-14-inch-m4-16gb-512gb.html?product_id=94086
22                                        /macbook-pro-14-inch-m4-16gb-512gb.html?product_id=94085
23                                     /laptop-hp-victus-15-fa1139tx-8y6w3pa.html?product_id=99129
24                                              /mac-mini-m4-2024-16gb-256gb.html?product_id=93963
25                               /laptop-asus-tuf-gaming-f15-fx507zc4-hn095w.html?product_id=82906
26                                      /laptop-lenovo-loq-15iax9-83gs000rvn.html?product_id=76752
27                                   /laptop-asus-vivobook-15-x1504za-nj517w.html?product_id=79241
28                                    /macbook-air-15-m3-24gb-512gb-2024-35w.html?product_id=95113
29                                    /macbook-air-15-m3-24gb-512gb-2024-35w.html?product_id=95114
30                                    /macbook-air-15-m3-24gb-512gb-2024-35w.html?product_id=95115
31                                    /macbook-air-15-m3-24gb-512gb-2024-35w.html?product_id=95112
32                           /laptop-gaming-acer-nitro-5-tiger-an515-58-52sp.html?product_id=42450
33                                 /laptop-acer-gaming-aspire-7-a715-76-53pj.html?product_id=71866
34                               /laptop-asus-gaming-vivobook-k3605zc-rp564w.html?product_id=86211
35                                 /macbook-pro-16-inch-m3-max-2023-48gb-1tb.html?product_id=73001
36                                 /macbook-pro-16-inch-m3-max-2023-48gb-1tb.html?product_id=73002
37                               /laptop-dell-inspiron-15-3520-5810blk-102f0.html?product_id=75068
38                                   /macbook-air-m2-2022-16gb-512gb-sac-70w.html?product_id=87617
39                                   /macbook-air-m2-2022-16gb-512gb-sac-70w.html?product_id=87618
40                                   /ma

In [ ]:
merged_df['url_path'] = merged_df.apply(
    lambda row: row['child_laptop_link'] if pd.notna(row['child_laptop_link']) else row['url_path'],
    axis=1
)

In [ ]:
print(f'Null: {merged_df["url_path"].isna().sum()}')

Null: 0


In [ ]:
# Add 'https://cellphones.com.vn' to url_path
merged_df['url_path'] = 'https://cellphones.com.vn' + merged_df['url_path']

In [ ]:
merged_df['url_path']

0                                  https://cellphones.com.vn/laptop-gaming-acer-nitro-v-anv15-51-58an.html?product_id=75444
1                                                  https://cellphones.com.vn/macbook-air-m2-2022-16gb.html?product_id=86461
2                                                  https://cellphones.com.vn/macbook-air-m2-2022-16gb.html?product_id=86460
3                                                  https://cellphones.com.vn/macbook-air-m2-2022-16gb.html?product_id=86462
4                                                  https://cellphones.com.vn/macbook-air-m2-2022-16gb.html?product_id=86459
5                       https://cellphones.com.vn/apple-macbook-air-13-m4-10cpu-8gpu-16gb-256gb-2025.html?product_id=101837
6                       https://cellphones.com.vn/apple-macbook-air-13-m4-10cpu-8gpu-16gb-256gb-2025.html?product_id=101838
7                       https://cellphones.com.vn/apple-macbook-air-13-m4-10cpu-8gpu-16gb-256gb-2025.html?product_id=101835
8                       https://cellphones.com.vn/apple-macbook-air-13-m4-10cpu-8gpu-16gb-256gb-2025.html?product_id=101836
9                                https://cellphones.com.vn/laptop-asus-tuf-gaming-a15-fa506ncr-hn047w.html?product_id=91455
10                                                https://cellphones.com.vn/laptop-hp-250-g9-ag2k7at.html?product_id=100666
11                                   https://cellphones.com.vn/macbook-air-m3-13-inch-2024-16gb-256gb.html?product_id=94501
12                                   https://cellphones.com.vn/macbook-air-m3-13-inch-2024-16gb-256gb.html?product_id=94504
13                                   https://cellphones.com.vn/macbook-air-m3-13-inch-2024-16gb-256gb.html?product_id=94503
14                                   https://cellphones.com.vn/macbook-air-m3-13-inch-2024-16gb-256gb.html?product_id=94502
15                                    https://cellphones.com.vn/laptop-acer-aspire-lite-al16-51p-55n7.html?product_id=87099
16                              https://cellphones.com.vn/laptop-asus-vivobook-14-oled-a1405va-km257w.html?product_id=79552
17                     https://cellphones.com.vn/apple-macbook-air-13-m4-10cpu-10gpu-16gb-512gb-2025.html?product_id=101843
18                     https://cellphones.com.vn/apple-macbook-air-13-m4-10cpu-10gpu-16gb-512gb-2025.html?product_id=101842
19                     https://cellphones.com.vn/apple-macbook-air-13-m4-10cpu-10gpu-16gb-512gb-2025.html?product_id=101841
20                     https://cellphones.com.vn/apple-macbook-air-13-m4-10cpu-10gpu-16gb-512gb-2025.html?product_id=101840
21                                        https://cellphones.com.vn/macbook-pro-14-inch-m4-16gb-512gb.html?product_id=94086
22                                        https://cellphones.com.vn/macbook-pro-14-inch-m4-16gb-512gb.html?product_id=94085
23                                     https://cellphones.com.vn/laptop-hp-victus-15-fa1139tx-8y6w3pa.html?product_id=99129
24                                              https://cellphones.com.vn/mac-mini-m4-2024-16gb-256gb.html?product_id=93963
25                               https://cellphones.com.vn/laptop-asus-tuf-gaming-f15-fx507zc4-hn095w.html?product_id=82906
26                                      https://cellphones.com.vn/laptop-lenovo-loq-15iax9-83gs000rvn.html?product_id=76752
27                                   https://cellphones.com.vn/laptop-asus-vivobook-15-x1504za-nj517w.html?product_id=79241
28                                    https://cellphones.com.vn/macbook-air-15-m3-24gb-512gb-2024-35w.html?product_id=95113
29                                    https://cellphones.com.vn/macbook-air-15-m3-24gb-512gb-2024-35w.html?product_id=95114
30                                    https://cellphones.com.vn/macbook-air-15-m3-24gb-512gb-2024-35w.html?product_id=95115
31                                    https://cellphones.com.vn/macbook-air-15-m3-24gb-512gb-2024-35w.html?product_id=95112
32                           htt

In [ ]:
merged_df.drop(columns =[['url_key','child_laptop_link']], inplace=True)

## image & child_laptop_image

In [ ]:
merged_df['image'] = merged_df.apply(
    lambda row: row['child_laptop_image'] if pd.notna(row['child_laptop_image']) else row['image'],
    axis=1
)

In [ ]:
merged_df.drop(columns =['child_laptop_image'], inplace=True)

## child_laptop_color

In [ ]:
merged_df.rename(columns={'child_laptop_color': 'laptop_color'}, inplace=True)
merged_df['laptop_color'] = merged_df['laptop_color'].str.lower()
merged_df['laptop_color'].fillna('đen', inplace=True)

<ipython-input-28-ae3b63fbf940>:3: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  merged_df['laptop_color'].fillna('đen', inplace=True)


## root_price, discounted_price & child_laptop_price

In [ ]:
merged_df[['root_price','discounted_price','child_laptop_price']]

root_price  discounted_price child_laptop_price
0     21490000.0        16390000.0        16.990.000₫
1     24990000.0        21190000.0        21.390.000₫
2     24990000.0        21190000.0        21.790.000₫
3     24990000.0        21190000.0        21.090.000₫
4     24990000.0        21190000.0        21.790.000₫
5     26990000.0        26390000.0        26.990.000₫
6     26990000.0        26390000.0        26.490.000₫
7     26990000.0        26390000.0        26.990.000₫
8     26990000.0        26390000.0        26.990.000₫
9     23490000.0        19090000.0        19.490.000₫
10    19190000.0        14590000.0        14.990.000₫
11    27990000.0        24490000.0        24.690.000₫
12    27990000.0        24490000.0        24.690.000₫
13    27990000.0        24490000.0        24.690.000₫
14    27990000.0        24490000.0        24.690.000₫
15    14990000.0        12891000.0        13.290.000₫
16    20990000.0        16590000.0        16.990.000₫
17    31990000.0        31490000.0        31.990.000₫
18    31990000.0        31490000.0        31.990.000₫
19    31990000.0        31490000.0        31.990.000₫
20    31990000.0        31490000.0        31.990.000₫
21    39990000.0        39090000.0        39.590.000₫
22    39990000.0        39090000.0        39.590.000₫
23    24590000.0        17590000.0        16.790.000₫
24    14990000.0        14055000.0        14.290.000₫
25    24990000.0        19390000.0        19.790.000₫
26    26990000.0        24090000.0        24.490.000₫
27    16490000.0        13390000.0        13.990.000₫
28    42990000.0        37490000.0        35.490.000₫
29    42990000.0        37490000.0        35.490.000₫
30    42990000.0        37490000.0        35.490.000₫
31    42990000.0        37490000.0        35.490.000₫
32    27990000.0        18590000.0        18.490.000₫
33    16990000.0        13390000.0        13.990.000₫
34    25290000.0        18090000.0        17.490.000₫
35   102490000.0        83490000.0        83.990.000₫
36   102490000.0        83490000.0        83.990.000₫
37    13990000.0        12115000.0        12.490.000₫
38    29990000.0        26990000.0        27.490.000₫
39    29990000.0        26990000.0        27.490.000₫
40    29990000.0        26990000.0        27.490.000₫
41    29990000.0        26990000.0        27.490.000₫
42    19990000.0        17590000.0        17.990.000₫
43    49990000.0        48490000.0        48.990.000₫
44    49990000.0        48490000.0        48.990.000₫
45    15990000.0        11630000.0        11.590.000₫
46    20990000.0        16890000.0        16.990.000₫
47    36990000.0        26590000.0        27.990.000₫
48    19190000.0        14590000.0        15.690.000₫
49    14490000.0        13090000.0        13.490.000₫
50    27490000.0        23490000.0        23.990.000₫
51    27490000.0        23490000.0        23.990.000₫
52    27490000.0        23490000.0        23.990.000₫
53    27490000.0        23490000.0        23.990.000₫
54    23490000.0        19090000.0        19.490.000₫
55    17990000.0        15090000.0        15.990.000₫
56    28990000.0        24590000.0        25.990.000₫
57    22690000.0        17590000.0        17.990.000₫
58    15490000.0        13890000.0        14.290.000₫
59    21290000.0        16590000.0        17.490.000₫
60    20990000.0        16590000.0        16.490.000₫
61    34990000.0        31290000.0        30.990.000₫
62    44000000.0        27590000.0        26.990.000₫
63    24990000.0        21590000.0        22.490.000₫
64    14990000.0         9690000.0         9.990.000₫
65    38990000.0        24590000.0                NaN
66    18490000.0        12600000.0        12.790.000₫
67    29990000.0        26990000.0        27.490.000₫
68    29990000.0        26990000.0        27.490.000₫
69    29990000.0        26990000.0        27.490.000₫
70    29990000.0        26990000.0        27.490.000₫
71    21990000.0        19590000.0        20.290.000₫
72    40990000.0        34590000.0        35.490.000₫
73    5799

In [ ]:
def clear_unit(text):
  if pd.isna(text):
    return None
  match = text.replace('₫','').replace('.', '').strip()
  return int(match)

In [ ]:
merged_df['child_laptop_price'] = merged_df['child_laptop_price'].apply(clear_unit)
def choose_best_price(row):
    child_price = row['child_laptop_price']
    discounted_price = row['discounted_price']

    # If discounted_price is NaN or child_price is less than discounted
    if pd.isna(discounted_price):
      if pd.isna(child_price):
        return None
      else:
        return child_price
    elif pd.isna(child_price):
      if pd.isna(discounted_price):
        return None
      else:
        return discounted_price
    elif child_price < discounted_price:
        return child_price
    else:
        return discounted_price

merged_df['discounted_price'] = merged_df.apply(choose_best_price, axis=1)


In [ ]:
merged_df[['root_price','discounted_price','child_laptop_price']]

root_price  discounted_price  child_laptop_price
0     21490000.0        16390000.0          16990000.0
1     24990000.0        21190000.0          21390000.0
2     24990000.0        21190000.0          21790000.0
3     24990000.0        21090000.0          21090000.0
4     24990000.0        21190000.0          21790000.0
5     26990000.0        26390000.0          26990000.0
6     26990000.0        26390000.0          26490000.0
7     26990000.0        26390000.0          26990000.0
8     26990000.0        26390000.0          26990000.0
9     23490000.0        19090000.0          19490000.0
10    19190000.0        14590000.0          14990000.0
11    27990000.0        24490000.0          24690000.0
12    27990000.0        24490000.0          24690000.0
13    27990000.0        24490000.0          24690000.0
14    27990000.0        24490000.0          24690000.0
15    14990000.0        12891000.0          13290000.0
16    20990000.0        16590000.0          16990000.0
17    31990000.0        31490000.0          31990000.0
18    31990000.0        31490000.0          31990000.0
19    31990000.0        31490000.0          31990000.0
20    31990000.0        31490000.0          31990000.0
21    39990000.0        39090000.0          39590000.0
22    39990000.0        39090000.0          39590000.0
23    24590000.0        16790000.0          16790000.0
24    14990000.0        14055000.0          14290000.0
25    24990000.0        19390000.0          19790000.0
26    26990000.0        24090000.0          24490000.0
27    16490000.0        13390000.0          13990000.0
28    42990000.0        35490000.0          35490000.0
29    42990000.0        35490000.0          35490000.0
30    42990000.0        35490000.0          35490000.0
31    42990000.0        35490000.0          35490000.0
32    27990000.0        18490000.0          18490000.0
33    16990000.0        13390000.0          13990000.0
34    25290000.0        17490000.0          17490000.0
35   102490000.0        83490000.0          83990000.0
36   102490000.0        83490000.0          83990000.0
37    13990000.0        12115000.0          12490000.0
38    29990000.0        26990000.0          27490000.0
39    29990000.0        26990000.0          27490000.0
40    29990000.0        26990000.0          27490000.0
41    29990000.0        26990000.0          27490000.0
42    19990000.0        17590000.0          17990000.0
43    49990000.0        48490000.0          48990000.0
44    49990000.0        48490000.0          48990000.0
45    15990000.0        11590000.0          11590000.0
46    20990000.0        16890000.0          16990000.0
47    36990000.0        26590000.0          27990000.0
48    19190000.0        14590000.0          15690000.0
49    14490000.0        13090000.0          13490000.0
50    27490000.0        23490000.0          23990000.0
51    27490000.0        23490000.0          23990000.0
52    27490000.0        23490000.0          23990000.0
53    27490000.0        23490000.0          23990000.0
54    23490000.0        19090000.0          19490000.0
55    17990000.0        15090000.0          15990000.0
56    28990000.0        24590000.0          25990000.0
57    22690000.0        17590000.0          17990000.0
58    15490000.0        13890000.0          14290000.0
59    21290000.0        16590000.0          17490000.0
60    20990000.0        16490000.0          16490000.0
61    34990000.0        30990000.0          30990000.0
62    44000000.0        26990000.0          26990000.0
63    24990000.0        21590000.0          22490000.0
64    14990000.0         9690000.0           9990000.0
65    38990000.0        24590000.0                 NaN
66    18490000.0        12600000.0          12790000.0
67    29990000.0        26990000.0          27490000.0
68    29990000.0        26990000.0          27490000.0
69    29990000.0        26990000.0          27490000.0
70    29990000.0        26990000.0          27490000.0
71    21990000.0        19590000.0          20

In [ ]:
merged_df.drop(columns =['child_laptop_price'], inplace=True)

In [ ]:
print(f'Null: {merged_df["discounted_price"].isna().sum()}')

Null: 224


In [ ]:
print(f'Null: {merged_df["root_price"].isna().sum()}')

Null: 228


## key_selling_points & child_features

In [ ]:
merged_df[['key_selling_points', 'special_features']]

key_selling_points  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       ['CPU Intel Core i5-13420H cân mọi tựa game từ AAA đến game Esport.', 'GPU GeForce RTX 2050 mới nhất cho đồ họa cực đỉnh, chiến mọi tựa game với mức cài đặt cao.', 'RAM 16 GB DDR5 5200Mhz, khả năng xử lý đa nhiệm và đa tác vụ của máy càng được tăng tốc tối đa.', 'Màn hình 15.6 inch Full HD, tần số quét chuẩn chiến game 144Hz.', 'Ổ cứng 512GB PCIE rộng rãi, lưu mọi tựa game dễ dàng.']   
1                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         ['Thiết kế sang trọng, lịch lãm - siêu mỏng 11.3mm, chỉ 1.24kg', 'Hiệu năng hàng đầu - Chip Apple m2, 8 nhân GPU, hỗ trợ tốt các phần mềm như Word, Axel, Adoble Premier', 'Đa nhiệm mượt mà - Ram 16GB, SSD 256GB cho phép vừa làm việc, vừa nghe nhạc', 'Màn hình sắc nét - Độ phân giải 2560 x 1664 cùng độ sáng 500 nits', 'Âm thanh sống động - 4 loa tramg bị công nghệ dolby atmos và âm thanh đa chiều']   
2                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         ['Thiết kế sang trọng, lịch lãm - siêu mỏng 11.3mm, chỉ 1.24kg', 'Hiệu năng hàng đầu - Chip Apple m2, 8 nhân GPU, hỗ trợ tốt các phần mềm như Word, Axel, Adoble Premier', 'Đa nhiệm mượt mà - Ram 16GB, SSD 256GB cho phép vừa làm việc, vừa nghe nhạc', 'Màn hình sắc nét - Độ phân giải 2560 x 1664 cùng độ sáng 500 nits', 'Âm thanh sống động - 4 loa tramg bị công nghệ dolby atmos và âm thanh đa chiều']   
3                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         ['Thiết kế sang trọng, lịch lãm - siêu mỏng 11.3mm, chỉ 1.24kg', 'Hiệu năng hàng đầu - Chip Apple m2, 8 nhân GPU, hỗ trợ tốt các phần mềm như Word, Axel, Adoble Premier', 'Đa nhiệm mượt mà - Ram 16GB, SSD 256GB cho phép vừa làm việc, vừa nghe nhạc', 'Màn hình sắc nét - Độ phân giải 2560 x 1664

In [ ]:
print(f'Null: {merged_df["key_selling_points"].isna().sum()}')
print(f'Null: {merged_df["special_features"].isna().sum()}')

Null: 0
Null: 146


In [ ]:
merged_df.drop(columns=['special_features'], inplace=True)

In [ ]:
overview_merged_v1 = pd.DataFrame({
    "Column name": merged_df.columns,
    "Data type":merged_df.dtypes,
    "Null count": merged_df.isnull().sum().values,
    'Null %': (merged_df.isnull().sum().values/ merged_df.shape[0]*100 ).round(2),
    "Unique count": merged_df.nunique()
})
overview_merged_v1.reset_index(drop=True, inplace=True)
overview_merged_v1




Column name Data type  Null count  Null %  Unique count
0                  product_id   float64           0    0.00           903
1                        name    object           0    0.00           897
2                       image    object           0    0.00           734
3                display_size   float64           0    0.00            23
4                  storage_gb   float64           0    0.00            10
5          key_selling_points    object           0    0.00           666
6                     cam_ung     int64           0    0.00             2
7                    material    object           0    0.00             3
8      laptop_special_feature    object           0    0.00            70
9            laptop_nganh_hoc    object           0    0.00             7
10                ram_storage   float64           0    0.00            13
11            ram_max_support   float64           0    0.00            14
12              product_state    object           0    0.00            10
13        storage_max_support   float64           0    0.00            16
14            nhu_cau_su_dung    object           0    0.00            29
15               manufacturer    object           0    0.00            15
16               filter_label    object           0    0.00           673
17                  cpu_brand    object           0    0.00             4
18             is_installment     int64           0    0.00             2
19                  filter_id    object           0    0.00           207
20              warranty_info    object           0    0.00            15
21             product_weight   float64           0    0.00           147
22                   url_path    object           0    0.00           903
23                    url_key    object           0    0.00           737
24                 os_version    object           0    0.00             6
25              display_width   float64           0    0.00            15
26                  vga_brand    object           0    0.00             5
27          bluetooth_version   float64           0    0.00            10
28              has_bluetooth     int64           0    0.00             2
29             display_height   float64           0    0.00            21
30                   ram_type    object           0    0.00            11
31                 cpu_series    object           0    0.00            40
32              o_cung_laptop    object           1    0.11           357
33                   vga_type    object          13    1.44             2
34                ports_slots    object          13    1.44           535
35                   width_mm   float64          83    9.19           169
36                  height_mm   float64          90    9.97           194
37                   depth_mm   float64         102   11.30           110
38               display_type    object          74    8.19           415
39           battery_capacity   float64          95   10.52            74
40              laptop_camera    object          79    8.75             2
41  laptop_cong_nghe_am_thanh    object         101   11.18           324
42                  ram_slots   float64         117   12.96             5
43                  cpu_model    object         283   31.34           150
44                  ram_speed    object         149   16.50            37
45                  cpu_cores   float64         160   17.72            12
46    laptop_tam_nen_man_hinh    object         288   31.89             8
47                 root_price   float64         228   25.25           151
48           discounted_price   float64         224   24.81           233
49              cpu_max_speed   float64         417   46.18            30
50               refresh_rate   float64         409   45.29             9
51                cpu_threads   float64         526   58.25            14
52                  cpu_speed   float64         542   60.02            35
53                   v

In [ ]:
merged_df.shape

(903, 57)

In [ ]:
!mkdir -p output

In [ ]:
merged_df.to_csv('output/general_info_v4.csv', index=False)